# Variography

In [ ]:
import geolime as geo
from pyproj import CRS
import numpy as np
import pyvista as pv

pv.set_jupyter_backend('panel')


geo.Project().set_crs(CRS("EPSG:20350"))

In [ ]:
dh = geo.read_file("../data/dh_pop_classif.geo")

In [ ]:
dh.user_properties()

In [ ]:
dh.regions()

## Data Selection 

In [ ]:
domain_solid = geo.datasets.load("rocklea_dome/domain_mesh.dxf")
domain_solid.name

In [ ]:
domain_solid.contains(dh)

In [ ]:
domain_solid_pv = domain_solid.to_pyvista()
dh_pv = dh.to_pyvista('in_OreZone')

In [ ]:
plotter = pv.Plotter()

plotter.add_mesh(domain_solid_pv, style="wireframe")
plotter.add_mesh(dh_pv.tube(radius=20))

plotter.set_scale(zscale=10)
plotter.show()

In [ ]:
geo.histogram_plot(data=[{"object":dh, "property":"Fe_pct", "region":"in_OreZone"}])

In [ ]:
dh.set_region_condition("HighGrade", "in_OreZone and (Fe_pct == Fe_pct)")

## VarioMap

In [ ]:
lags, tol = geo.generate_lags(lag=200, plag=50, nlags=15)

In [ ]:
geo.vario_map(
    geo_object=dh,
    attribute="Fe_pct",
    region="HighGrade",
    lags=lags,
    tol=tol,
    n_az=15,
    atol=35
)

In [ ]:
geo.vario_contour(
    geo_object=dh,
    attribute="Fe_pct",
    region="HighGrade",
    lags=lags,
    tol=tol,
    n_az=15,
    atol=35
)

VarioMap suggets major and minor preferential direction are N00 and N90.

In [ ]:
major_direction = 0.
minor_direction = 90.

## Fitting a Covariance Model

### Model the Nugget Effect

#### Experimental Downhole Variogram

In [ ]:
lags_bh, tol_bh = geo.generate_lags(lag=1., plag=50, nlags=10.)

In [ ]:
tol_bh

In [ ]:
vario_exp_bh = geo.variogram(
    object=dh,
    attribute="Fe_pct",
    region="HighGrade",
    geographic_azimuth=0,
    dip=90,
    pitch=90,
    lags=lags_bh,
    tol=tol_bh,
    atol=10
)

geo.plot_semivariogram(
    variograms=[vario_exp_bh],
    display_npairs=True
)

In [ ]:
vario_exp_bh

#### Automatic Fitting

In [ ]:
nugget_model = geo.Nugget() + geo.Spherical()

In [ ]:
geo.model_fit(
    variograms=[vario_exp_bh], 
    cov=nugget_model
)

In [ ]:
geo.plot_semivariogram(
    variograms=[vario_exp_bh],
    model=nugget_model,
    model_angles=[{"azi":0, "dip":90, "pitch":90}],
    display_npairs=True
)

In [ ]:
print(nugget_model)

In [ ]:
nugget_value = nugget_model.cov_elem_list[0].sill

### Model the Sphericals

#### Experimental Variograms along the XY plane

In [ ]:
lags, tol = geo.generate_lags(lag=50, plag=50, nlags=10)

In [ ]:
vario_exp_major = geo.variogram(
    object=dh,
    attribute="Fe_pct",
    region="HighGrade",
    geographic_azimuth=major_direction,
    dip=0,
    pitch=0,
    lags=lags,
    tol=tol,
    atol=40
)
vario_exp_minor = geo.variogram(
    object=dh,
    attribute="Fe_pct",
    region="HighGrade",
    geographic_azimuth=minor_direction,
    dip=0,
    pitch=0,
    lags=lags,
    tol=tol,
    atol=30
)

geo.plot_semivariogram(
    variograms=[vario_exp_major, vario_exp_minor],
    display_npairs=True
)

#### Automatic Fitting

In [ ]:
model =  geo.Nugget() + geo.Spherical() + geo.Spherical()

In [ ]:
short_range_spherical_ratio = 0.7
long_range_spherical_ratio = 0.3

In [ ]:
geo.model_fit(
    variograms=[
        vario_exp_major, 
        vario_exp_minor, 
        vario_exp_bh
    ], 
    cov=model,
    constraints=[
        {"sill_fixed":nugget_value},
        {
            "sill_max": short_range_spherical_ratio * (vario_exp_major.attrs["variable_var"] - nugget_value),
            "angle_fixed_0": major_direction,
            "angle_fixed_1": 0,
            "angle_fixed_2": 0
        },
        {
            "sill_max": long_range_spherical_ratio * (vario_exp_major.attrs["variable_var"] - nugget_value),
            "angle_fixed_0": major_direction,
            "angle_fixed_1": 0,
            "angle_fixed_2": 0,
        }
    ]
)

In [ ]:
geo.plot_semivariogram(
    variograms=[
        vario_exp_major, 
        vario_exp_minor, 
        vario_exp_bh
    ],
    model=model,
    model_angles=[{"azi":major_direction, "dip":0, "pitch":0}, {"azi":minor_direction, "dip":0, "pitch":0}, {"azi":0, "dip":90, "pitch":90}],
    display_npairs=True
)

In [ ]:
print(model)